In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt

In [2]:
def calculate_time_difference(time1: str, time2: str) -> int:
    def convert_str_time_to_int(time: str) -> int:
        splitted_time = time.split(':')
        return int(splitted_time[2]) + int(splitted_time[1]) * 60 + int(splitted_time[0]) * 3600
    return convert_str_time_to_int(time= time2) - convert_str_time_to_int(time= time1) + 5

In [3]:
def extract_coordinates(raw_lat, raw_lon):
    lat = round(float(raw_lat),6)
    lon = round(float(raw_lon),6)
    return (lon,lat)

In [4]:
stops = pd.read_csv('stops.txt', low_memory=False)
#pathways = pd.read_csv('pathways.txt', low_memory=False)
routes = pd.read_csv('routes.txt', low_memory=False)
trips = pd.read_csv('trips.txt', low_memory=False)
#shapes = pd.read_csv('shapes.txt', low_memory=False)
stop_times = pd.read_csv('stop_times.txt', low_memory=False)

In [5]:
#Remove unnecessary columns
stops = stops[['stop_id','stop_name','stop_lat','stop_lon']]
trips = trips[['route_id','trip_id','service_id','direction_id']]
routes = routes[['route_id','route_short_name','route_desc','route_color']]
stop_times = stop_times[['trip_id','stop_id','arrival_time','departure_time']]

In [6]:
#Joining routes and trips
routes_info = pd.merge(trips, routes, on=['route_id'])
routes_info.head()

route_id    trip_id          service_id  direction_id route_short_name  \
0     5200   B1914710  B19147EVVHPBP-0011             0               M2   
1     5200  B19147100  B19147EVVHPBP-0011             1               M2   
2     5200  B19147101  B19147EVVHPBP-0011             0               M2   
3     5200  B19147102  B19147EVVHPBP-0011             1               M2   
4     5200  B19147103  B19147EVVHPBP-0011             0               M2   

                               route_desc route_color  
0  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
1  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
2  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
3  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
4  Déli pályaudvar M / Örs vezér tere M+H      E41F18

In [7]:
#Joining stop_times and stops
detailed_stops = pd.merge(stops,stop_times, on=['stop_id'])
detailed_stops.head()

stop_id       stop_name  stop_lat   stop_lon    trip_id arrival_time  \
0  004903  Örs vezér tere  47.50348  19.137211   C2206010     17:12:00   
1  004903  Örs vezér tere  47.50348  19.137211  C22060102     15:42:00   
2  004903  Örs vezér tere  47.50348  19.137211  C22060103     16:00:00   
3  004903  Örs vezér tere  47.50348  19.137211  C22060104     17:42:00   
4  004903  Örs vezér tere  47.50348  19.137211  C22060105     18:00:00   

  departure_time  
0       17:12:00  
1       15:42:00  
2       16:00:00  
3       17:42:00  
4       18:00:00

In [8]:
#Joining all data together
dataset = pd.merge(routes_info,detailed_stops, on=['trip_id'])
dataset.head()

route_id   trip_id          service_id  direction_id route_short_name  \
0     5200  B1914710  B19147EVVHPBP-0011             0               M2   
1     5200  B1914710  B19147EVVHPBP-0011             0               M2   
2     5200  B1914710  B19147EVVHPBP-0011             0               M2   
3     5200  B1914710  B19147EVVHPBP-0011             0               M2   
4     5200  B1914710  B19147EVVHPBP-0011             0               M2   

                               route_desc route_color stop_id  \
0  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00063   
1  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00094   
2  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00959   
3  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00961   
4  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F01019   

           stop_name   stop_lat   stop_lon arrival_time departure_time  
0      Batthyány tér  47.506826  19.038103     07:51:37       07:51:37  
1    Déli pályaudvar  47.500450  19.024604     07:48:15       07:48:15  
2  Kossuth Lajos tér  47.505511  19.045769     07:53:00       07:53:00  
3    Deák Ferenc tér  47.497593  19.053857     07:55:00       07:55:00  
4            Astoria  47.494825  19.062457     07:56:35       07:56:35

In [9]:
#Problem with database
(dataset.loc[dataset['stop_name'] == 'Batthyány tér M+H']).stop_id.unique()

array(['044590', 'F00064', '067592', '008750', 'F00057', 'F00067',
       '037379', 'F00059', 'F00066'], dtype=object)

In [10]:
#Get all unique trips
all_lines = dataset.trip_id.unique()
all_lines.shape

(274452,)

In [11]:
#number of unique routes
all_routes = dataset.route_id.unique()
all_routes.shape

(348,)

In [12]:
# Getting unique trip_ids, randomly from one day. (not the first service by day)
unique_trip_ids = []

#For testing: 
#for route in all_routes[:MAX_ROUTES]: #MAX_ROUTES can be 25-30-50 for better performance
for route in all_routes:
    selected_route_df = (dataset.loc[dataset['route_id'] == str(route)])
    all_trips = selected_route_df.trip_id.unique()
    unique_trip_ids.append(all_trips[0])

In [13]:
def generate_data_for_network(dataframe):
    station_name_labels = {}
    station_name_labels[dataframe['stop_id'][0]] = [dataframe['stop_name'][0]][0]
    station_positions = {}
    station_positions[dataframe['stop_id'][0]] = extract_coordinates(dataframe['stop_lat'][0],dataframe['stop_lon'][0])
    edges = []
    edge_labels = {}
    edge_colors = []
    for i in range(1,len(dataframe)):

        #Get current station name
        station_name_labels[dataframe['stop_id'][i]] = [dataframe['stop_name'][i]][0]

        #Getting nodes (departure, arrival)
        departure, arrival = dataframe['stop_id'][i-1], dataframe['stop_id'][i]

        #Calculating time difference, aka weights
        previous_arrival_time, arrival_time = dataframe['arrival_time'][i-1],dataframe['arrival_time'][i]
        time_difference = calculate_time_difference(time1= previous_arrival_time, time2= arrival_time)
        
        #Getting coordinates
        station_positions[dataframe['stop_id'][i]] = extract_coordinates(dataframe['stop_lat'][i],dataframe['stop_lon'][i])

        #Adding edges with weights (starting node, ending node, weight)
        edges.append((departure,arrival,time_difference))

        #Adding edge labels
        edge_labels[(departure,arrival)] = [dataframe['route_short_name'][i]][0]

        #Adding edge colors
        edge_colors.append(('#'+[dataframe['route_color'][i]][0]))
    
    #Return values: station name labels (node labels), edges, edge labels, edge colors, node positions
    return (station_name_labels,edges,edge_labels,edge_colors,station_positions)

In [14]:
G = nx.DiGraph()

#station_name_labels,edges,edge_labels,edge_colors

station_name_labels = {}
station_node_positions = {}
edges = []
edge_labels = {}
edge_colors = []

for trip_id in unique_trip_ids:
    trip_data = (dataset.loc[dataset['trip_id'] == trip_id]).sort_values('arrival_time')
    trip_data.reset_index(drop=True, inplace=True)
    
    res = generate_data_for_network(trip_data)
    station_name_labels.update(res[0])
    edges.extend(res[1])
    edge_labels.update(res[2])
    edge_colors.extend(res[3])
    station_node_positions.update(res[4])

#plt.figure()
fig = plt.figure(figsize=(140,140))
G.add_weighted_edges_from(edges);
nx.draw(G,pos=station_node_positions,labels = station_name_labels,font_size=7, edge_color=edge_colors,node_size=25)
nx.draw_networkx_edge_labels(G,station_node_positions,edge_labels=edge_labels,font_size=7,font_color='red')

plt.axis('off')
#plt.show()
plt.savefig('bkk_network.pdf')

In [15]:
len(G.nodes)


3930